In [1]:
import ROOT
import glob
ROOT.gROOT.ProcessLine(".L FTFunctions.cpp")
ROOT.gInterpreter.Declare("""
    const UInt_t barWidth = 60;
    ULong64_t processed = 0, totalEvents = 0;
    std::string progressBar;
    std::mutex barMutex; 
    auto registerEvents = [](ULong64_t nIncrement) {totalEvents += nIncrement;};
    ROOT::RDF::RResultPtr<ULong64_t> AddProgressBar(ROOT::RDF::RNode df, int everyN=10000, int totalN=100000) {
        registerEvents(totalN);
        auto c = df.Count();
        c.OnPartialResultSlot(everyN, [everyN] (unsigned int slot, ULong64_t &cnt){
            std::lock_guard<std::mutex> l(barMutex);
            processed += everyN; //everyN captured by value for this lambda
            progressBar = "[";
            for(UInt_t i = 0; i < static_cast<UInt_t>(static_cast<Float_t>(processed)/totalEvents*barWidth); ++i){
                progressBar.push_back('|');
            }
            // escape the '\' when defined in python string
            std::cout << "\\r" << std::left << std::setw(barWidth) << progressBar << "] " << processed << "/" << totalEvents << std::flush;
        });
        return c;
    }
""")
# Enables multithreading
useRange = True
if not useRange:
    nThreads = 8
    ROOT.ROOT.EnableImplicitMT(nThreads)

Welcome to JupyROOT 6.24/00


In [2]:
listOfFilesData = glob.glob("/eos/user/m/migordon/Skims/NANOv8/UL18/SingleMuon/*/*_Skim.root")
listOfFilesMonteCarloTTToSemiLeptonic = glob.glob("/eos/user/m/migordon/Skims/NANOv8/UL18/TTToSemiLeptonic_TuneCP5_13TeV-powheg-pythia8/*_Skim.root")
listOfFilesMonteCarloTTTo2L2Nu = glob.glob("/eos/user/m/migordon/Skims/NANOv8/UL18/TTTo2L2Nu_TuneCP5_13TeV-powheg-pythia8/*_Skim.root")

listOfFilesMonteCarloTTToSemiLeptonic = listOfFilesMonteCarloTTToSemiLeptonic[0:3]
listOfFilesMonteCarloTTTo2L2Nu = listOfFilesMonteCarloTTTo2L2Nu[0:3]

dictOfListOfFiles = {"Data" : listOfFilesData, "MonteCarloTTToSemiLeptonic" : listOfFilesMonteCarloTTToSemiLeptonic, "MonteCarloTTTo2L2Nu" : listOfFilesMonteCarloTTTo2L2Nu} 

In [3]:
chain = {}
meta = {}
rdf = {}
mrdf = {}
nevents = {}
sumweight = {}
neventsVal = {}
rdfTriggersAndMasks = {}
rdfOnePlusMuons = {}
rdfJetVariables = {}
rdfTwoPlusJets = {}
rdfNoMuTrigger = {}
rdfmuOneBTaggedJet = {}
rdfmu = {}
rdfOtherMuons = {}
hist = {}
report = {}

for sample, fileList in dictOfListOfFiles.items():
    
    if sample == 'Data':
        vecList = ROOT.std.vector(str)()

        for element in dictOfListOfFiles['Data']:
            vecList.push_back(element)

        rdf['Data'] = ROOT.ROOT.RDataFrame("Events", vecList)    
        #mureport['Data'] = rdf['Data'].Report()
        print(rdf['Data'].Report())
        mrdf['Data'] = ROOT.ROOT.RDataFrame("Runs", vecList)

        if useRange:
            rdf['Data'] = rdf['Data'].Range(4800000)
            nrange = 4800000
            printcode = ' if(rdfentry_ % 5000 == 0) { std::cout << "Processed entry " << rdfentry_ << "/' + str(nrange) + '" << std::endl; } return rdfentry_;'
            
            rdf['Data'] = rdf['Data'].Define("my_rdfentry", printcode)
            
            s = rdf['Data'].Min('my_rdfentry')
                         
            c = rdf['Data'].Count()
                                
            c.GetValue()
        
    else:   
        chain[sample] = ROOT.TChain("Events")
        meta[sample] = ROOT.TChain("Runs")

        for file in fileList:
            #print(file, end=" ")
            
            chain[sample].Add(file)
            meta[sample].Add(file)

        rdf[sample] = ROOT.ROOT.RDataFrame(chain[sample])
        mrdf[sample] = ROOT.ROOT.RDataFrame(meta[sample])

        if useRange:
            rdf[sample] = rdf[sample].Range(500000000)
        
        nevents[sample] = mrdf[sample].Sum("genEventCount")
        sumweight[sample] = mrdf[sample].Sum("genEventSumw")
    
        #print(nevents[sample].GetValue())
        #print(sumweight[sample].GetValue())
        neventsVal[sample] = nevents[sample].GetValue()

<cppyy.gbl.ROOT.RDF.RResultPtr<ROOT::RDF::RCutFlowReport> object at 0xb28c210>
Processed entry 0/4800000
Processed entry 5000/4800000
Processed entry 10000/4800000
Processed entry 15000/4800000
Processed entry 20000/4800000
Processed entry 25000/4800000
Processed entry 30000/4800000
Processed entry 35000/4800000
Processed entry 40000/4800000
Processed entry 45000/4800000
Processed entry 50000/4800000
Processed entry 55000/4800000
Processed entry 60000/4800000
Processed entry 65000/4800000
Processed entry 70000/4800000
Processed entry 75000/4800000
Processed entry 80000/4800000
Processed entry 85000/4800000
Processed entry 90000/4800000
Processed entry 95000/4800000
Processed entry 100000/4800000
Processed entry 105000/4800000
Processed entry 110000/4800000
Processed entry 115000/4800000
Processed entry 120000/4800000
Processed entry 125000/4800000
Processed entry 130000/4800000
Processed entry 135000/4800000
Processed entry 140000/4800000
Processed entry 145000/4800000
Processed entry 

Warning in <TClass::Init>: no dictionary for class edm::Hash<1> is available
Warning in <TClass::Init>: no dictionary for class edm::ParameterSetBlob is available
Warning in <TClass::Init>: no dictionary for class edm::ProcessHistory is available
Warning in <TClass::Init>: no dictionary for class edm::ProcessConfiguration is available
Warning in <TClass::Init>: no dictionary for class __pair_base<edm::Hash<1>,edm::ParameterSetBlob> is available
Warning in <TClass::Init>: no dictionary for class pair<edm::Hash<1>,edm::ParameterSetBlob> is available


In [4]:
#Semileptonic ttbar xsection: 364.3109
#Single mu trigger for 2017 (B,C,D,E,F): "HLT_IsoMu27"
#"HLT_Ele35_WPTight_Gsf"
#lumiDict = {"2017": 41.53, "2018": 59.97}
wgtFormula = {}

# wgtFormula used to weight each event
# XS = Literature Cross section of the process of interest (in picobarnes; the 1000 converts to femotobarnes), lumi = presumed luminosity of the data one is normalizing against; XS * lumi = # of expected events;
# genWeight = quantity stored in every event which comes from the Monte Carlo generator telling you what the value of the generated event is (usually close to 1); it can be + or -; it also contains matching
#     effeciency; tells you the Monte Carlo defined value of the event
# sW = sum of weights; normalizes the genWeight
lumiDict = {"2018": 59.97 * (4800000/10000000)} #  brilcalc lumi --normtag /cvmfs/cms-bril.cern.ch/cms-lumi-pog/Normtags/normtag_PHYSICS.json -u /fb --begin 302031 --end 302663 --hltpath "HLT_IsoMu27*"
wgtFormula['Data'] = "1"
wgtFormula['MonteCarloTTToSemiLeptonic'] = "{XS:f} * {lumi:f} * 1000 * genWeight / {sW:f}".format(XS=364.31, lumi=lumiDict["2018"], sW=float(sumweight['MonteCarloTTToSemiLeptonic'].GetValue()))
wgtFormula['MonteCarloTTTo2L2Nu'] = "{XS:f} * {lumi:f} * 1000 * genWeight / {sW:f}".format(XS=87.33, lumi=lumiDict["2018"], sW=float(sumweight['MonteCarloTTTo2L2Nu'].GetValue()))
#wgtFormula['WJetsToLNu'] = "{XS:f} * {lumi:f} * 1000 * genWeight / {sW:f}".format(XS=61526.7, lumi=lumiDict["2018"], sW=float(sumweight['WJetsToLNu'].GetValue()))

In [5]:
cpp_code = """
typedef ROOT::VecOps::RVec<Float_t>                        RVec_f;
typedef ROOT::VecOps::RVec<Int_t>                          RVec_i;
typedef ROOT::VecOps::RVec<Long_t>                         RVec_l;

class MatchOppositelyChargedMuons
{
    private:
        RVec_f Muon_pt;
        RVec_f Muon_eta;
        RVec_f Muon_phi;
        RVec_f Muon_mass;
        RVec_i Muon_charge;
        long EventNumber;


    public:
        MatchOppositelyChargedMuons(RVec_f Muon_pt, RVec_f Muon_eta, RVec_f Muon_phi, RVec_f Muon_mass, RVec_i Muon_charge, long EventNumber);
        RVec_f InvariantMassCalculator();
};

MatchOppositelyChargedMuons::MatchOppositelyChargedMuons(RVec_f Muon_pt, RVec_f Muon_eta, RVec_f Muon_phi, RVec_f Muon_mass, RVec_i Muon_charge, long EventNumber)
{
    this->Muon_pt = Muon_pt;
    this->Muon_eta = Muon_eta;
    this->Muon_phi = Muon_phi;
    this->Muon_mass = Muon_mass;
    this->Muon_charge = Muon_charge;
    this->EventNumber = EventNumber;
}


/* This function matches each muon with oppositely charged muons. */
RVec_f MatchOppositelyChargedMuons::InvariantMassCalculator()
{ 
    RVec_f pt {};
    RVec_f eta {};
    RVec_f phi {};
    RVec_f mass {};
    
    float FirstMuonCharge = 0;
    float SecondMuonCharge = 0;
    
    RVec_f InvariantMasses {};
    
    float im = 0;
        
    /* Loop over the set of muons to determine which muons have +1 charge, then match them with all the ones with -1 charge. */
    for(int i = 0; i < this->Muon_charge.size(); i++)
    {
        FirstMuonCharge = this->Muon_charge[i];
        
        /* If charges are opposite, calculate the invariant mass of them */
        for(int j = i+1; j < this->Muon_charge.size(); j++)
        {
            SecondMuonCharge = this->Muon_charge[j];
            
            if(FirstMuonCharge * SecondMuonCharge == -1)
            {
                pt.push_back(Muon_pt[i]);
                eta.push_back(Muon_eta[i]);
                phi.push_back(Muon_phi[i]);
                mass.push_back(Muon_mass[i]);
                    
                pt.push_back(Muon_pt[j]);
                eta.push_back(Muon_eta[j]);
                phi.push_back(Muon_phi[j]);
                mass.push_back(Muon_mass[j]);
                    
                im = ROOT::VecOps::InvariantMass(pt, eta, phi, mass);
                
                InvariantMasses.push_back(im);
                    
                pt.clear();
                eta.clear();
                phi.clear();
                mass.clear();
            }
        }
    }
        
    return InvariantMasses;
}
"""

ROOT.gInterpreter.Declare(cpp_code)

#rvf = ROOT.VecOps.RVec(float)([2.71,3.14])
#rvi = ROOT.VecOps.RVec(int)([1,-1])

#x = ROOT.MatchOppositelyChargedMuons(rvf, rvf, rvf, rvf, rvi, 123456789)
#print(x.InvariantMassCalculator())

True

In [6]:
# Object selection (masks) and cuts (filters)
# LumiXS is lumi * xs
#.Define("Junk", 'if(rdfentry_ % 200000 == 0){ std::cout << "Processed " << rdfentry_ << " entries on slot " << rdfslot_ << std::endl;} return rdfentry_;')

# Initial cuts for finding muons, isolated or not.
for sample in dictOfListOfFiles:
    rdfTriggersAndMasks[sample] = rdf[sample].Filter("HLT_IsoMu27 == true", "HLTTriggerSingleMuonTrigger").Define("LumiXS",wgtFormula[sample])\
        .Define("mu_mask", "Muon_pt > 30 && abs(Muon_eta) < 2.4 && Muon_tightId == true && Muon_pfIsoId >= 4")\
        .Define("mu_veto", "Muon_pt > 10 && abs(Muon_eta) < 2.4 && Muon_looseId == true && Muon_pfIsoId >= 4 && mu_mask == false")\
        .Define("jpsi_mu_candidate_mask", "Muon_pt > 3 && Muon_mediumId == true && mu_mask == false")
    rdfOnePlusMuons[sample] = rdfTriggersAndMasks[sample].Filter("Sum(mu_mask) == 1", "Exactly One Good Muon")\
        .Define("SMuon_pt", "Muon_pt[mu_mask]")\
        .Define("SMuon_eta", "Muon_eta[mu_mask]")\
        .Define("SMuon_phi", "Muon_phi[mu_mask]")\
        .Define("SMuon_mass", "Muon_mass[mu_mask]")\
        .Define("SMuon_pfRelIso03_all", "Muon_pfRelIso03_all[mu_mask]")\
        .Define("SMuon_pfRelIso03_chg", "Muon_pfRelIso03_chg[mu_mask]")\
        .Define("SMuon_pfRelIso04_all", "Muon_pfRelIso04_all[mu_mask]")
    rdfJetVariables[sample] = rdfOnePlusMuons[sample]\
        .Define("jet_mask", "ROOT::VecOps::RVec<Int_t> jmask = (Jet_pt >= 30 && abs(Jet_eta) <= 2.5 && Jet_jetId >= 2); "\
                          "for(int i=0; i < SMuon_pt.size(); ++i){"\
                              "ROOT::VecOps::RVec<Float_t> dr;"\
                              "for(int j=0; j < jmask.size(); ++j){"\
                                  "dr.push_back(ROOT::VecOps::DeltaR(Jet_eta.at(j), SMuon_eta.at(i), Jet_phi.at(j), SMuon_phi.at(i)));}"\
                                  "jmask = jmask && dr >= 0.4;"\
                                  "dr.clear();}"\
                          "return jmask;")\
        .Define("MediumBJetMask", "Jet_btagDeepFlavB > 0.3033 && jet_mask" )\
        .Define("MTofMETandMu", "FTA::transverseMassMET(SMuon_pt, SMuon_phi, SMuon_mass, MET_pt, MET_phi)")\
        .Define("Num_Jets", "Jet_pt[jet_mask].size()")\
        .Define("SJet1_pt", "Jet_pt[jet_mask].size() > 0 ? Jet_pt[jet_mask].at(0) : -500")\
        .Define("SJet2_pt", "Jet_pt[jet_mask].size() > 1 ? Jet_pt[jet_mask].at(1) : -500")\
        .Define("SJet1_eta", "Jet_eta[jet_mask].size() > 0 ? Jet_eta[jet_mask].at(0) : 500")\
        .Define("SJet2_eta", "Jet_eta[jet_mask].size() > 1 ? Jet_eta[jet_mask].at(1) : 500")\
        .Define("SJet1_phi", "Jet_phi[jet_mask].size() > 0 ? Jet_phi[jet_mask].at(0) : 500")\
        .Define("SJet2_phi", "Jet_phi[jet_mask].size() > 1 ? Jet_phi[jet_mask].at(1) : 500")\
        .Define("SJet_btagDeepFlavB", "Jet_btagDeepFlavB[jet_mask]")\
        .Define("Num_BTaggedJets", "Sum(MediumBJetMask)")\
        .Define("Ht", "Sum(Jet_pt[jet_mask])")
    rdfTwoPlusJets[sample] = rdfJetVariables[sample].Filter("Num_Jets >= 4", "At Least Four Jets")\
        .Define("DeepJetB", "Jet_pt[jet_mask].size() > 0 ? Jet_btagDeepFlavB[jet_mask].at(0) : 0")\
        .Define("Num_Muons", "Muon_pt[mu_mask].size()")
    rdfmuOneBTaggedJet[sample] = rdfTwoPlusJets[sample].Filter("Num_BTaggedJets >= 1", "At Least One B-Tagged Jet")
    rdfmu[sample] = rdfmuOneBTaggedJet[sample].Filter("Sum(mu_veto) == 0", "No Vetoed Muons")

    rdfOtherMuons[sample] = rdfTriggersAndMasks[sample].Filter("Sum(jpsi_mu_candidate_mask) >= 2", "JPsi Candidate")\
        .Define("InvariantMasses", "std::cout << rdfentry_ << std::endl; auto c = MatchOppositelyChargedMuons(Muon_pt, Muon_eta, Muon_phi, Muon_mass, Muon_charge, event); return c.InvariantMassCalculator();")

In [7]:
for sample in dictOfListOfFiles:
    
    if sample not in hist.keys():
        hist[sample] = {}
        report[sample] = rdf[sample].Report()
        
    if sample == 'Data':
        
        hist['Data']["mu_pt"] = rdfmu['Data'].Histo1D(("mu_pt","Muon Transverse Momentum; Pt (GeV);Events",100,20,220),"SMuon_pt")
        hist['Data']["mu_eta"] = rdfmu['Data'].Histo1D(("mu_eta", "Muon Pseudorapidity; Eta; Events",100,-3,3),"SMuon_eta")
        hist['Data']["mu_phi"] = rdfmu['Data'].Histo1D(("mu_phi", "Muon Angle; Phi (Radians); Events",100,-3.5,3.5),"SMuon_phi")
        hist['Data']["jet1_pt"] = rdfmu['Data'].Histo1D(("jet1_pt", "Jet Transverse Momentum for Leading Jet; Pt (GeV); Events", 100, 20, 200), "SJet1_pt")
        hist['Data']["jet2_pt"] = rdfmu['Data'].Histo1D(("jet2_pt", "Jet Transverse Momentum for Subleading Jet; Pt (GeV); Events", 100, 20, 200), "SJet2_pt")
        hist['Data']["jet1_eta"] = rdfmu['Data'].Histo1D(("jet1_eta", "Jet Pseudorapidity for Leading Jet; Eta; Events", 100, -3, 3), "SJet1_eta")
        hist['Data']["jet2_eta"] = rdfmu['Data'].Histo1D(("jet2_eta", "Jet Pseudorapidity for Subleading Jet; Eta; Events", 100, -3, 3), "SJet2_eta")
        hist['Data']["jet1_phi"] = rdfmu['Data'].Histo1D(("jet1_phi", "Jet Angle for Leading Jet; Phi (Radians); Events", 100, -3.5, 3.5), "SJet1_phi")
        hist['Data']["jet2_phi"] = rdfmu['Data'].Histo1D(("jet2_phi", "Jet Angle for Subleading Jet; Phi (Radians); Events", 100, -3.5, 3.5), "SJet2_phi")
        hist['Data']["jet_deep"] = rdfmu['Data'].Histo1D(("jet_deep", "Deep Jet B Discriminator; Discriminant Value; Events", 100, 0, 1), "DeepJetB")
        hist['Data']["number_of_jets"] = rdfmu['Data'].Histo1D(("number_of_jets", "Number of Jets; Number Of Jets; Events", 20, 0, 20), "Num_Jets") 
        hist['Data']["number_of_muons"] = rdfmu['Data'].Histo1D(("number_of_muons", "Number of Muons; Number of Muons; Events", 5, 0, 5), "Num_Muons")
        hist['Data']["transverse_mass"] = rdfmu['Data'].Histo1D(("transverse_mass", "Transverse Mass; Transverse Mass (GeV); Events", 150, 0, 150), "MTofMETandMu")
        hist['Data']["missing_transverse_momentum"] = rdfmu['Data'].Histo1D(("missing_transverse_momentum", "Missing Transverse Momentum; Missing Transverse Momentum(GeV); Events", 150, 0, 300), "MET_pt")
        hist['Data']["ht"] = rdfmu['Data'].Histo1D(("ht", "Ht; Ht; Events", 300, 0, 1500), "Ht")
        hist['Data']["muon_pfRelIso03_all"] = rdfmu['Data'].Histo1D(("muon_pfRelIso03_all", "Muon Pf Rel Iso 03 (All); Muon Pf Rel Iso 03 (All); Events", 60, 0, .3), "SMuon_pfRelIso03_all")
        hist['Data']["muon_pfRelIso03_chg"] = rdfmu['Data'].Histo1D(("muon_pfRelIso03_chg", "Muon Pf Rel Iso 03 (Chg); Muon Pf Rel Iso 03 (Chg); Events", 60, 0, .3), "SMuon_pfRelIso03_chg")
        hist['Data']["muon_pfRelIso04_all"] = rdfmu['Data'].Histo1D(("muon_pfRelIso04_all", "Muon Pf Rel Iso 04 (All); Muon Pf Rel Iso 04 (All); Events", 60, 0, .3), "SMuon_pfRelIso04_all")
        hist['Data']["invariant_masses"] = rdfOtherMuons['Data'].Histo1D(("invariant_masses", "Invariant Masses; Invariant Masses; Events", 50, .5, 12), "InvariantMasses")        
        hist['Data']["invariant_masses_zoomed"] = rdfOtherMuons['Data'].Histo1D(("invariant_masses_zoomed", "Invariant Masses; Invariant Masses; Events", 50, 2.8, 3.4), "InvariantMasses")

    else:
        
        hist[sample]["mu_pt"] = rdfmu[sample].Histo1D((sample + "_" + "mu_pt","Monte Carlo " + sample + ";Pt (GeV);Events",100,20,220),"SMuon_pt","LumiXS")
        hist[sample]["mu_eta"] = rdfmu[sample].Histo1D((sample + "_" + "mu_eta", "Monte Carlo " + sample + "; Eta; Events",100,-3,3),"SMuon_eta","LumiXS")
        hist[sample]["mu_phi"] = rdfmu[sample].Histo1D((sample + "_" + "mu_phi", "Monte Carlo " + sample + "; Phi (Radians); Events",100,-3.5,3.5),"SMuon_phi","LumiXS")
        hist[sample]["jet1_pt"] = rdfmu[sample].Histo1D((sample + "_" + "jet1_pt", "Monte Carlo " + sample + "; Pt (GeV); Events", 100, 20, 200), "SJet1_pt", "LumiXS")
        hist[sample]["jet2_pt"] = rdfmu[sample].Histo1D((sample + "_" + "jet2_pt", "Monte Carlo " + sample + "; Pt (GeV); Events", 100, 20, 200), "SJet2_pt", "LumiXS")
        hist[sample]["jet1_eta"] = rdfmu[sample].Histo1D((sample + "_" + "jet1_eta", "Monte Carlo " + sample + "; Eta; Events", 100, -3, 3), "SJet1_eta", "LumiXS")
        hist[sample]["jet2_eta"] = rdfmu[sample].Histo1D((sample + "_" + "jet2_eta", "Monte Carlo " + sample +"; Eta; Events", 100, -3, 3), "SJet2_eta", "LumiXS")
        hist[sample]["jet1_phi"] = rdfmu[sample].Histo1D((sample + "_" + "jet1_phi", "Monte Carlo " + sample + "; Phi (Radians); Events", 100, -3.5, 3.5), "SJet1_phi", "LumiXS")
        hist[sample]["jet2_phi"] = rdfmu[sample].Histo1D((sample + "_" + "jet2_phi", "Monte Carlo " + sample +"; Phi (Radians); Events", 100, -3.5, 3.5), "SJet2_phi", "LumiXS")
        hist[sample]["jet_deep"] = rdfmu[sample].Histo1D((sample + "_" + "jet_deep", "Monte Carlo " + sample +"; Discriminant Value; Events", 100, 0, 1), "DeepJetB", "LumiXS")
        hist[sample]["number_of_jets"] = rdfmu[sample].Histo1D((sample + "_" + "number_of_jets", "Monte Carlo " + sample +"; Number Of Jets; Events", 20, 0, 20), "Num_Jets", "LumiXS") 
        hist[sample]["number_of_muons"] = rdfmu[sample].Histo1D((sample + "_" + "number_of_muons", "Monte Carlo " + sample +"; Number of Muons; Events", 5, 0, 5), "Num_Muons", "LumiXS")
        hist[sample]["transverse_mass"] = rdfmu[sample].Histo1D((sample + "_" + "transverse_mass", "Monte Carlo " + sample +"; Transverse Mass (GeV); Events", 150, 0, 150), "MTofMETandMu", "LumiXS")
        hist[sample]["missing_transverse_momentum"] = rdfmu[sample].Histo1D((sample + "_" + "missing_transverse_momentum", "Monte Carlo" + sample + "; Missing Transverse Momentum(GeV); Events", 150, 0, 300), "MET_pt", "LumiXS")
        hist[sample]["ht"] = rdfmu[sample].Histo1D((sample + "_" + "ht", "Monte Carlo " + sample + "; Ht; Events", 300, 0, 1500), "Ht", "LumiXS")
        hist[sample]["muon_pfRelIso03_all"] = rdfmu[sample].Histo1D((sample + "_" + "muon_pfRelIso03_all", "Monte Carlo " + sample + "; Muon Pf Rel Iso 03 (All); Events", 60, 0, .3), "SMuon_pfRelIso03_all", "LumiXS")
        hist[sample]["muon_pfRelIso03_chg"] = rdfmu[sample].Histo1D((sample + "_" + "muon_pfRelIso03_chg", "Monte Carlo " + sample + "; Muon Pf Rel Iso 03 (Chg); Events", 60, 0, .3), "SMuon_pfRelIso03_chg", "LumiXS")
        hist[sample]["muon_pfRelIso04_all"] = rdfmu[sample].Histo1D((sample + "_" + "muon_pfRelIso04_all", "Monte Carlo " + sample + "; Muon Pf Rel Iso 04 (All); Events", 60, 0, .3), "SMuon_pfRelIso04_all", "LumiXS")
        hist[sample]["invariant_masses"] = rdfOtherMuons[sample].Histo1D((sample + "_" + "invariant_masses", "Monte Carlo " + sample + "; Invariant Masses; Invariant Masses; Events", 50, .5, 12), "InvariantMasses", "LumiXS")
        hist[sample]["invariant_masses_zoomed"] = rdfOtherMuons[sample].Histo1D((sample + "_" + "invariant_masses_zoomed", "Monte Carlo " + sample + "; Invariant Masses; Invariant Masses; Events", 50, 2.8, 3.4), "InvariantMasses", "LumiXS")

In [8]:
for sample in dictOfListOfFiles:

    ROOT.RDF.SaveGraph(rdf[sample], str(sample) + ".dot")

In [9]:
for sample in dictOfListOfFiles:
    cutflow = report[sample].GetValue()
    cutflow.Print()
    
    era = "2018"
    process = sample
    channel = "Mu"
    syst = "nominal"

    outFile = ROOT.TFile.Open("{}_{}_{}.root".format(era, channel, process), "RECREATE")
    for name, hist_pointer in hist[sample].items():
        print(hist_pointer)
        hist_value = hist_pointer.GetValue()
        
        hist_value.SetName("{}___{}___{}___{}___{}".format(era, channel, process, name, syst))
        print(hist_value)
        hist_value.Write()

    outFile.Close()

<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0xd807110>
Name: 2018___Mu___Data___mu_pt___nominal Title: Muon Transverse Momentum NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0xd7ffce0>
Name: 2018___Mu___Data___mu_eta___nominal Title: Muon Pseudorapidity NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x15e1cda0>
Name: 2018___Mu___Data___mu_phi___nominal Title: Muon Angle NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x12c92be0>
Name: 2018___Mu___Data___jet1_pt___nominal Title: Jet Transverse Momentum for Leading Jet NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x12efd5e0>
Name: 2018___Mu___Data___jet2_pt___nominal Title: Jet Transverse Momentum for Subleading Jet NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x12fdd0f0>
Name: 2018___Mu___Data___jet1_eta___nominal Title: Jet Pseudorapidity for Leading Jet NbinsX: 100
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x12d0fb10>
Name: 2018___Mu___Data___jet2_eta___nominal Ti

<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x160242f0>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___number_of_jets___nominal Title: Monte Carlo MonteCarloTTTo2L2Nu NbinsX: 20
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x160251d0>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___number_of_muons___nominal Title: Monte Carlo MonteCarloTTTo2L2Nu NbinsX: 5
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x15e58980>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___transverse_mass___nominal Title: Monte Carlo MonteCarloTTTo2L2Nu NbinsX: 150
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x15e3c0c0>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___missing_transverse_momentum___nominal Title: Monte CarloMonteCarloTTTo2L2Nu NbinsX: 150
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x15e609f0>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___ht___nominal Title: Monte Carlo MonteCarloTTTo2L2Nu NbinsX: 300
<cppyy.gbl.ROOT.RDF.RResultPtr<TH1D> object at 0x15f96440>
Name: 2018___Mu___MonteCarloTTTo2L2Nu___muon_pfRelIso03_all___nomin